In [38]:
from mpl_toolkits.mplot3d import Axes3D
import matplotlib.pyplot as plt
import numpy as np
from matplotlib import cm

s = 3.157e7    # Seconds in a year
sigma = 5.6e-8 # Stefan Boltzmann  in W/m^2*K^4
K = 2.8        # Conductance of rock in W/m/K
t0 = 10000     # Initial temperature of rock in K
p = 5515       # Density of rock in kg/m^3
c = 800        # Specific Heat in J/kg/K

R = 6371000    # Radius of Earth in m

N = 100
T = np.zeros((N,N))

X = np.linspace(0, R, N)
Y = np.linspace(0, R, N)
X, Y = np.meshgrid(X, Y)

dx = R/N
dy = R/N
dt = np.floor(0.25*(dx**2)/(2*K))
print(dt/s)

for i in range(0,N):
    for j in range(0,N):
        if np.sqrt(((i-N/2)**2)+((j-N/2)**2)) < N/2:
            T[i,j] = t0 - (t0/N)*np.sqrt(((N/2 - i)**2)+((N/2 - j)**2))

#plt.imshow(T)
#plt.show()

5.73974513778904


In [39]:
def iter2D(T):
    Tnew = np.zeros((N,N))
    for i in range(0,N):
        for j in range(0,N):
            
            # Heat Conduction within the planet
            if np.sqrt(((i-N/2)**2)+((j-N/2)**2)) < N/2 - 1:
                Tnew[i,j] = T[i,j] + (K*dt/(dx**2))*(T[i,j+1] - 2*T[i,j] + T[i,j-1]) + (K*dt/(dy**2))*(T[i+1,j] - 2*T[i,j] + T[i-1,j]) 
                
            # BC on surface
            if np.sqrt(((i-N/2)**2)+((j-N/2)**2)) < N/2 \
            and np.sqrt(((i-N/2)**2)+((j-N/2)**2)) > N/2 - 1:
                Tnew[i,j] = T[i,j] - (dt*sigma * (T[i,j]**4))/((2*np.pi*R/N) * p * c)
    return Tnew

def HeatTotal(T):
    cols = [sum(T[i,:]) for i in range(0,np.shape(T)[0])]
    s = sum(cols)
    return s

In [40]:
(2*K*dt/(dx**2))

0.24999999935944248

In [41]:
q0 = HeatTotal(T)
print(q0)

%matplotlib osx
fig = plt.figure(dpi=150, figsize=(8,4))
T1 = np.copy(T)

from matplotlib.animation import FFMpegWriter
writer = FFMpegWriter(fps=50)

t = 5000
with writer.saving(fig, "FinalResult.mp4", dpi=150):
    for i in range(0,t):
        Ti = iter2D(T)
        T = np.copy(Ti)
    
        if (i%10==0): print(i,end='')
        print('.',end='')
    
        fig.clear()
        
        plt.subplot(121, projection='3d')
        ax = fig.gca(projection='3d')
        ax.plot_surface(X, Y, T, cmap=cm.coolwarm, antialiased=False)
        
        plt.subplot(122)
        plt.imshow(T, cmap=cm.coolwarm)
        plt.colorbar()
        
        plt.draw()
        plt.pause(0.05)
        writer.grab_frame()
print('Done.')
        
qf = HeatTotal(T)
print('Heat lost:', (q0-qf)/q0, 'percent')
print('Time elapsed:', dt*t/s, 'years')

52214875.691047
0..........10..........20..........30..........40..........50..........60..........70..........80..........90..........100..........110..........120..........130..........140..........150..........160..........170..........180..........190..........200..........210..........220..........230..........240..........250..........260..........270..........280..........290..........300..........310..........320..........330..........340..........350..........360..........370..........380..........390..........400..........410..........420..........430..........440..........450..........460..........470..........480..........490..........500..........510..........520..........530..........540..........550..........560..........570..........580..........590..........600..........610..........620..........630..........640..........650..........660..........670..........680..........690..........700..........710..........720..........730..........740..........750..........760....